# Run pre-trained DeepSeek Coder 1.3B Model on Chat-GPT 4o generated dataset

## First load dataset into pandas dataframe

In [2]:
import pandas as pd 
import warnings
warnings.filterwarnings("ignore")

# Load dataset and check length
df = pd.read_csv("./train-data/sql_train.tsv", sep='\t')
print("Total dataset examples: " + str(len(df)))
print("\n")

# Test sampling
sample = df.sample(n=1)
print(sample["natural_query"].values[0])
print(sample["sql_query"].values[0])
print(sample["result"].values[0])

Total dataset examples: 1044


Which team had the largest lead in a single game in the 2001 season?
SELECT g.team_name_home AS team, os.largest_lead_home AS lead FROM other_stats os JOIN game g ON os.game_id = g.game_id WHERE g.season_id = '22001' ORDER BY os.largest_lead_home DESC LIMIT 1;
Portland Trail Blazers|47


## Load pre-trained DeepSeek model using transformers and pytorch packages

In [3]:
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch

# Set device to cuda if available, otherwise CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load model and tokenizer
tokenizer = AutoTokenizer.from_pretrained("./deepseek-coder-1.3b-instruct")
model = AutoModelForCausalLM.from_pretrained("./deepseek-coder-1.3b-instruct", torch_dtype=torch.bfloat16, device_map=device) 
model.generation_config.pad_token_id = tokenizer.pad_token_id

## Create prompt to setup the model for better performance

In [19]:
from src.prompts.prompt import input_text

## Test model performance on a single example

In [5]:
# Create message with sample query and run model
message=[{ 'role': 'user', 'content': input_text + sample["natural_query"].values[0]}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

# Print output
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
print(query_output)

SQLite:
SELECT team_abbreviation_home FROM other_stats WHERE lead_changes = 1 AND season_id = '2001';



# Test sample output on sqlite3 database

In [17]:
import sqlite3 as sql

# Create connection to sqlite3 database
connection = sql.connect('./nba-data/nba.sqlite')
cursor = connection.cursor()

# Execute query from model output and print result
if query_output[0:7] == "SQLite:":
    print("cleaned")
    query = query_output[7:]
elif query_output[0:4] == "SQL:":
    query = query_output[4:]
else:
    query = query_output

try:
    cursor.execute(query)
    rows = cursor.fetchall()
    for row in rows:
        print(row)
except:
    pass

cleaned


## Create function to compare output to ground truth result from examples

In [ ]:
import math
from src.evaluation.compare_result import compare_result_two

def compare_result(sample_query, sample_result, query_output):
    # Clean model output to only have the query output
    if query_output[0:7] == "SQLite:":
        query = query_output[7:]
    elif query_output[0:4] == "SQL:":
        query = query_output[4:]
    else:
        query = query_output
    
    # Try to execute query, if it fails, then this is a failure of the model
    try:
        # Execute query and obtain result
        cursor.execute(query)
        rows = cursor.fetchall()

        # Strip all whitespace before comparing queries since there may be differences in spacing, newlines, tabs, etc.
        query = query.replace(" ", "").replace("\n", "").replace("\t", "")
        sample_query = sample_query.replace(" ", "").replace("\n", "").replace("\t", "")
        query_match = (query == sample_query)

        # If the queries match, the results clearly also match
        if query_match:
            return True, True, True

        # Check if this is a multi-line query
        if "|" in sample_result or "(" in sample_result:
            #print(rows)
            # Create list of results by stripping separators and splitting on them
            if "(" in sample_result:
                sample_result = sample_result.replace("(", "").replace(")", "")
                result_list = sample_result.split(",") 
            else:
                result_list = sample_result.split("|") 

            # Strip all results in list
            for i in range(len(result_list)):
                result_list[i] = str(result_list[i]).strip()
            
            # Loop through model result and see if it matches training example
            result = False
            for row in rows:
                for r in row:
                    for res in result_list:
                        try:
                            if math.isclose(float(r), float(res), abs_tol=0.5):
                                return True, query_match, True
                        except:
                            if r in res or res in r:
                                return True, query_match, True
                    
            # Check if the model returned a sum of examples as opposed to the whole thing
            if len(rows) == 1:
                for r in rows[0]:
                    if r == str(len(result_list)):
                        return True, query_match, True
                    
            return True, query_match, result
        # Else the sample result is a single value or string
        else:
            #print(rows)
            result = False
            # Loop through model result and see if it contains the sample result
            for row in rows:
                for r in row:
                    # Check by string
                    if str(r) in str(sample_result):
                        try:
                            if math.isclose(float(r), float(sample_result), abs_tol=0.5):
                                return True, query_match, True
                        except:
                            return True, query_match, True
                    # Check by number, using try incase the cast as float fails
                    try:
                        if math.isclose(float(r), float(sample_result), abs_tol=0.5):
                            return True, query_match, True
                    except:
                        pass

            # Check if the model returned a list of examples instead of a total sum (both acceptable)
            try:
                if len(rows) > 1 and len(rows) == int(sample_result):
                    return True, query_match, True
                if len(rows[0]) > 1 and rows[0][1] is not None and  len(rows[0]) == int(sample_result):
                    return True, query_match, True
            except:
                pass

            # Compare results and return
            return True, query_match, result
    except:
        return False, False, False

# Obtain sample
sample = df.sample(n=1)
sample_dic = {
    "natural_query": "How many home games did the Miami Heat play in the 2021 season?",
    "sql_query": "SELECT COUNT(*) FROM game WHERE team_name_home = 'Miami Heat' AND season_id = '22021';",
    "result": 41.0
}

sample = pd.DataFrame([sample_dic])
"""
print(sample["natural_query"].values[0])
print(sample["sql_query"].values[0])
print(sample["result"].values[0])
"""

# Create message with sample query and run model
message=[{ 'role': 'user', 'content': input_text + sample["natural_query"].values[0]}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

# Print output
query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
print(query_output)

result = compare_result(sample["sql_query"].values[0], sample["result"].values[0], query_output)
print("Statement valid? " + str(result[0]))
print("SQLite matched? " + str(result[1]))
print("Result matched? " + str(result[2]))

result_two = compare_result_two(cursor, sample["sql_query"].values[0], sample["result"].values[0], query_output)
print("Statement valid? " + str(result_two[0]))
print("SQLite matched? " + str(result_two[1]))
print("Result matched? " + str(result_two[2]))

ImportError: cannot import name 'compare_result_two' from 'src.evaluation.compare_result' (/Users/esteban/Documents/USC/spring_2025/NLP/SQL-Generation/src/evaluation/compare_result.py)

## Create function to evaluate pretrained model on full datasets

In [7]:
def run_evaluation(nba_df, title):
    counter = 0
    num_valid = 0
    num_sql_matched = 0
    num_result_matched = 0
    for index, row in nba_df.iterrows():
        # Create message with sample query and run model
        message=[{ 'role': 'user', 'content': input_text + row["natural_query"]}]
        inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)
        outputs = model.generate(inputs, max_new_tokens=512, do_sample=False, top_k=50, top_p=0.95, num_return_sequences=1, eos_token_id=tokenizer.eos_token_id)

        # Obtain output
        query_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

        # Evaluate model result
        valid, sql_matched, result_matched = compare_result(row["sql_query"], row["result"], query_output)
        if valid:
            num_valid += 1
        if sql_matched:
            num_sql_matched += 1
        if result_matched:
            num_result_matched += 1

        # Break after predefined number of examples
        counter += 1
        if counter % 50 == 0:
            print("Completed " + str(counter))

    # Print evaluation results
    print("\n" + title + " results:")
    print("Percent valid: " + str(num_valid / len(nba_df)))
    print("Percent SQLite matched: " + str(num_sql_matched / len(nba_df)))
    print("Percent result matched: " + str(num_result_matched / len(nba_df)))

# Evaluate on less than 90 dataset

In [9]:
less_than_90_df = pd.read_csv("./train-data/less_than_90.tsv", sep='\t')
run_evaluation(less_than_90_df, "Less than 90")
print("Dataset length: " + str(len(less_than_90_df)))

Completed 50
Completed 100
Completed 150
Completed 200

Less than 90 results:
Percent valid: 0.8448979591836735
Percent SQLite matched: 0.43673469387755104
Percent result matched: 0.6530612244897959
Dataset length: 245


# Evaluate on game table queries

In [10]:
game_queries = pd.read_csv("./train-data/queries_from_game.tsv", sep='\t')
run_evaluation(game_queries, "Queries from game")
print("Dataset length: " + str(len(game_queries)))

Completed 50
Completed 100
Completed 150
Completed 200
Completed 250
Completed 300
Completed 350
Completed 400
Completed 450
Completed 500
Completed 550
Completed 600
Completed 650
Completed 700
Completed 750
Completed 800

Queries from game results:
Percent valid: 0.7613365155131265
Percent SQLite matched: 0.13842482100238662
Percent result matched: 0.383054892601432
Dataset length: 838


## Evaluate on other stats queries

In [11]:
other_stats_queries = pd.read_csv("./train-data/queries_from_other_stats.tsv", sep='\t')
run_evaluation(other_stats_queries, "Queries from other stats")
print("Dataset length: " + str(len(other_stats_queries)))

Completed 50
Completed 100
Completed 150

Queries from other stats results:
Percent valid: 0.21428571428571427
Percent SQLite matched: 0.01948051948051948
Percent result matched: 0.07142857142857142
Dataset length: 154


## Evaluate on team queries

In [12]:
team_queries = pd.read_csv("./train-data/queries_from_team.tsv", sep='\t')
run_evaluation(team_queries, "Queries from team")
print("Dataset length: " + str(len(team_queries)))

Completed 50

Queries from team results:
Percent valid: 0.8653846153846154
Percent SQLite matched: 0.5961538461538461
Percent result matched: 0.7884615384615384
Dataset length: 52


## Evaluate on queries requiring join statements

In [13]:
join_queries = pd.read_csv("./train-data/with_join.tsv", sep='\t')
run_evaluation(join_queries, "Queries with join")
print("Dataset length: " + str(len(join_queries)))

Completed 50
Completed 100
Completed 150

Queries with join results:
Percent valid: 0.1945945945945946
Percent SQLite matched: 0.0
Percent result matched: 0.04864864864864865
Dataset length: 185


## Evaluate on queries not requiring join statements

In [14]:
no_join_queries = pd.read_csv("./train-data/without_join.tsv", sep='\t')
run_evaluation(no_join_queries, "Queries without join")
print("Dataset length: " + str(len(no_join_queries)))

Completed 50
Completed 100
Completed 150
Completed 200
Completed 250
Completed 300
Completed 350
Completed 400
Completed 450
Completed 500
Completed 550
Completed 600
Completed 650
Completed 700
Completed 750
Completed 800
Completed 850

Queries without join results:
Percent valid: 0.7916181606519208
Percent SQLite matched: 0.17462165308498254
Percent result matched: 0.42374854481955765
Dataset length: 859


## Evaluate on full training dataset

In [15]:
# Run evaluation on all training data
run_evaluation(df, "All training data")
print("Dataset length: " + str(len(df)))

Completed 50
Completed 100
Completed 150
Completed 200
Completed 250
Completed 300
Completed 350
Completed 400
Completed 450
Completed 500
Completed 550
Completed 600
Completed 650
Completed 700
Completed 750
Completed 800
Completed 850
Completed 900
Completed 950
Completed 1000

All training data results:
Percent valid: 0.685823754789272
Percent SQLite matched: 0.14367816091954022
Percent result matched: 0.35823754789272033
Dataset length: 1044
